# 0184934-付子乾 ——实验报告

# 筛选高新技术企业信息以及公司财报PDF的名称修正

In [1]:
import re
import pandas as pd
import json
import os
import shutil
import numpy as np
from IPython.display import display, HTML

In [2]:
# 指定文件地址，获取json型文件转为DataFrame
os.chdir(r'C:\Users\Xwindwaaaani\Desktop\Study\201学期\Python数据挖掘与分析')
obj_text = json.load(open('words_finding.json', encoding='utf-8'))
   
obj_df = pd.DataFrame(obj_text)

In [8]:
# 打开对应目录下文件，并获得index（用于后续遍历与索引）
firm_excel = pd.read_excel('2009_2019_创业公司.xlsx').loc[:, ['证券代码', '公告标题']].iloc[:-1, :]
firm_excel_index = firm_excel.loc[:, '公告标题'].index
obj_df_index = obj_df.loc[:, '证券代码'].index
# 提前定义DataFrame中的文件格式
obj_df['公司名称'] = 'N/a'
name_dict = {}
# 从创业公司中找到对应创业公司的证券代码，并存入obj_df中
for i in firm_excel_index:
    text = firm_excel.loc[i, '公告标题']
    security_code = firm_excel.loc[i, '证券代码']
    firm_name = re.findall(r'(.+?):', text, re.DOTALL)[0]
    name_dict[security_code] = firm_name

# 输出，这里只输出前20家公司为例
print('证券代码', '\t'*2, '公司名称')
for i in range(20):
    print(list(name_dict.keys())[i], '\t'*2, list(name_dict.values())[i])
for j in obj_df_index:
    code_code = obj_df.loc[j, '证券代码']
    try:
        obj_df.loc[j, '公司名称'] = name_dict[code_code]
    except:
        ## 这里可以添加爬虫
        print(code_code)

# display(HTML(obj_df.to_html()))

证券代码 		 公司名称
300352.SZ 		 北信源
300216.SZ 		 千山药机
300209.SZ 		 天泽信息
300731.SZ 		 科创新源
300055.SZ 		 万邦达
300343.SZ 		 联创节能
300278.SZ 		 华昌达
300093.SZ 		 金刚玻璃
300367.SZ 		 东方网力
300370.SZ 		 安控股份
300189.SZ 		 神农大丰
300347.SZ 		 泰格医药
300260.SZ 		 新莱应材
300362.SZ 		 天保重装
300220.SZ 		 金运激光
300598.SZ 		 诚迈科技
300311.SZ 		 任子行
300330.SZ 		 华虹计通
300148.SZ 		 天舟文化
300525.SZ 		 博思软件


In [9]:
## 添加新列(是否为高型企业及其对应的文本证明内容)
keys = []
for key, value in obj_df.loc[0, 'keywords_indexes'].items():
     keys.append(key) 

obj_df.loc[:, '是否为高新技术企业'] = np.zeros((len(obj_df), 1))
for index, key in enumerate(keys):
    obj_df.loc[:, key] = np.zeros((len(obj_df), 1))
    obj_df.loc[:, key+'evidence'] = np.zeros((len(obj_df), 1))

In [10]:
## 删除数据
# 由于部分数据缺失，导致对于该公司无法按年限分类（进一步导致无法正确的获取其路径名称来进一步修改），因此统一放入abandon_data数据列中
true_data = []
false_data = []
index2019 = []; index2018 = []; index2017 = []; index2016 = []; index2015 = []
obj_year = obj_df.loc[:, '年报年份']
for i in range(len(obj_df)):
    if re.match(r'\d',obj_year[i]):
        true_data.append(i)
        if obj_year[i] == '2019':
            index2019.append(i)
        elif obj_year[i] == '2018':
            index2018.append(i)
        elif obj_year[i] == '2017':
            index2017.append(i)
        elif obj_year[i] == '2016':
            index2016.append(i)
        elif obj_year[i] == '2015':
            index2015.append(i)
    else:
        false_data.append(i)

abandon_data = obj_df.iloc[false_data, :]
obj_df2 = obj_df.iloc[true_data, :]

In [11]:
## 归结年限分门别类，并汇总至一张总表中
obj_df2019 = obj_df.iloc[index2019, :].drop(columns = ['年报年份'])
obj_df2018 = obj_df.iloc[index2018, :].drop(columns = ['年报年份'])
obj_df2017 = obj_df.iloc[index2017, :].drop(columns = ['年报年份'])
obj_df2016 = obj_df.iloc[index2016, :].drop(columns = ['年报年份'])
obj_df2015 = obj_df.iloc[index2015, :].drop(columns = ['年报年份'])
Obj_list = [obj_df2015, obj_df2016, obj_df2017, obj_df2018, obj_df2019]

In [12]:
## 关键词定义，用于在文本中筛选文本证据
key_info = {'高新技术企业': ['批准','认定','证书编号','高新技术企业证书','颁发','获得'] 
            ,'技术中心': ['企业技术中心','技术中心建设','国家级企业技术中心','认定']
            ,'实验中心': ['实现中心获得','创新实验中心','动物实验中心','公司实验中心','扩建了','实验中心建设','企业实验中心']
            ,'工程中心': ['应用工程中心']
            ,'实验室': ['重点实验室','获得批准','实验室建设','实验室阶段','工程实验室','通过','中心实验室','研究实验室','实验室奖励','技术实验室','认可','认证','具备国家','设立','拥有'] # 切记主任、职业、专业、担任、学历、独立董事这个该死的东西
            ,'研究院': ['设立','通过','企业研究院','重点研究院','成立','公司研究院']
            ,'院士': ['院士']
            ,'博士后': ['博士后']
            ,'工作站': ['工作站']
            ,'研究中心': ['研究中心']
            ,'研发平台': ['研发平台']
            ,'研究基地': ['研究基地']
            ,'博士后工作站': ['博士后工作站']
            ,'科研工作站': ['科研工作站']
            ,'产学研': ['产学研']}

In [13]:
## error_info指的是误导性信息，这些信息用于进一步剔除有key_info筛选后的结果
error_info = ['主任','职业','专业','担任','学历','独立董事','委员']

In [14]:
## demo 一个测试的样本（未含错误信息的筛选）
obj_info = obj_df2019.loc[:, 'keywords_surrounding_strings']
indexes = obj_df2019.loc[:, 'keywords_surrounding_strings'].index
for i in range(len(obj_df2019)):
    obj_dict = obj_info.iloc[i]

    for key, value1 in obj_dict.items():
        info_evidence = []
        value2 = key_info[key]
        if len(value1) != 0:
            for item1 in value1:
                # key info
                for item2 in value2:
                    if item2 in item1:
                        info_evidence.append(item1)
                        break
        
        if len(info_evidence) != 0:
            
            obj_df2019.loc[indexes[i], key] = 1
            obj_df2019.loc[indexes[i], key+'evidence'] = str(info_evidence)
        else:
            obj_df2019.loc[indexes[i], key+'evidence'] = str([])

# 为了输出的美观性，这里至调整至20家公司
display(HTML(obj_df2019.iloc[:20, :].to_html()))


In [15]:
# 以上述Demo作为样板，定义函数
def info_filter(Data, Key_info, Error_info):
    obj_info = Data.loc[:, 'keywords_surrounding_strings']
    indexes = Data.loc[:, 'keywords_surrounding_strings'].index
    for i in range(len(Data)):
        obj_dict = obj_info.iloc[i]
    
        for key, value1 in obj_dict.items():
            info_evidence = []
            value2 = Key_info[key]
            if len(value1) != 0:
                for item1 in value1:
                    # key info
                    for item2 in value2:
                        for error in Error_info:
                            if item2 in item1 and error not in item1:
                                info_evidence.append(item1)
                                break
                
            if len(info_evidence) != 0:
                
                Data.loc[indexes[i], key] = 1
                Data.loc[indexes[i], key+'evidence'] = str(info_evidence)
            else:
                Data.loc[indexes[i], key+'evidence'] = str([])
    return Data

In [16]:
## 由于这个案例是已经做完了，所以无法进行处理，这里我就直接输出打印了
# file = pd.ExcelWriter(r"C:\Users\Xwindwaaaani\Desktop\Study\201学期\Python数据挖掘与分析\2015-2019高新技术企业-v2.xlsx")

# 正常的顺序应该是
# 1. 对对应年限的obj_df进行筛选，找到文本证据以及重填obj_df
# 2. 将obj_df存入ExcelWriter创建好的Excel中，生成一个sheet名为对应财年的sheet
# 3. 后在财报对应年限文件夹下创建新的文件夹，用于存在高性技术企业的财报
# 4. 在处理好的obj_df中找到是高新技术的企业获得其名称，以其名称配上对应路径获取公司财报路径，移动该财报至新文件夹
# 5. 若出现错误，生成错误信息，并存入Not_find_dict中


Not_find_dict = {}
for index, item in enumerate(Obj_list):
    os.chdir(r"C:\Users\Xwindwaaaani\Desktop\Study\201学期\Python数据挖掘与分析")
    year = str(index+2015)
    target_info = info_filter(item, key_info, error_info)

# 同样只输出20家公司的信息
display(HTML(target_info.iloc[:20,:].to_html()))
#     target_info.to_excel(file, sheet_name=year)
#     print('\n','-'*20,'\n',year+'年信息保存成功','\n','-'*20, '\n')
    ## 移动文件（把是高性技术企业的公司移入新的文件夹）
#     os.chdir(r'E:\政产学研平台\PDF_Source\{}'.format(year))
#     new_file = year+'年高新技术企业'
#     isExists = os.path.exists(new_file) 
#     if not isExists:
#         os.mkdir(new_file)
#         print(new_file+'创建成功')
#     ## 把文件名拿到手
#     mid_target_info = target_info[target_info['高新技术企业'] == 1].loc[:, '证券代码']
#     file_list = os.listdir(r'E:\政产学研平台\PDF_Source\{}'.format(year))
#     not_find_list = []
#     file_str = '_+_' + '_+_'.join(file_list) + '_+_'
#     for target in mid_target_info:
#         target = target[:6]
#         # 移动文件
#         try:
#             pdf_name = re.findall(r'\+_({}.+?)_\+'.format(target), file_str, re.DOTALL)[0]
#             shutil.move(pdf_name, new_file)
#         except:
#             not_find_list.append(target)
#             print(target+'并未找到相应的财报')
#     Not_find_dict[year] = not_find_list
    
# file.save()

## 下面是对pdf进行重命名的操作

In [17]:
## 同样的，由于那些文件已经操作好了，因此下面的内容就难以再输入，这里主要讲一下思路
# 由于数据量过大，运行时间长，这里采取的是一年一年处理
# 1. 获取该财年目录下的所有财报名称，生成一个myList
# 2. 对myList进行遍历，对pdf类文件进行处理
# 3. 如果该pdf的文件名后六位是证券代码，那么提示信息“已更改”，否则打开该财报，处理其文本（目的是得到其名称和代码）
# 4. 通过正则匹配，找到“第二节公司简介和主要财务指标”，获取其对应内容下的代码
# 5. 以代码+原文本冒号后内容为名称（如300005：2019年年度报告）给其命名，如果命名失败，那么返回错误信息（可能原因是某些pdf是图片格式，无法正常以pdfplumber访问
# 6. 保留新名称和旧的名称，进入下一次循环


old_nameD = {}; wrong_nameD = {}; Total_name = []
for year in range(2018, 2019):
    dirway = r'E:\政产学研平台\PDF_Source\{}'.format(str(year))
    os.chdir(dirway)
    myList = os.listdir(dirway)
    old_nameL = []; wrong_nameL = []
    for item in myList:
        if item[-4:] == '.pdf':
            if re.match(r'\d', item[:6]):
                print(item+'已更改')
                continue
            try:
                with pdfplumber.open(item) as pdf:
                    str_text = ''
                    for index, page in enumerate(pdf.pages[:20]):
                        str_text = str_text + page.extract_text()
                try:
                    mid_text1 = re.findall(r'第十节(.+)', str_text, re.DOTALL)[0]
                    mid_text1 = mid_text1.replace('\n', '').replace('\t', '').replace(' ', '')
                    mid_text2 = re.findall(r'第二节公司简介和主要财务指标(.+)', mid_text1, re.DOTALL)[0][:100]
                    firm_code = re.findall(r'股票代码(\d{6})', mid_text2, re.DOTALL)[0]
                    ## 重命名
                    new_name = firm_code + '：' + re.findall(r'：(.+)', item, re.DOTALL)[0]
                    os.rename(item, new_name)
                    old_nameL.append(item)
                    print(item+'已重命名')
                except:
                    print(item+'重命名失败')
            except:
                print(item+'内置格式可能不满足txt形式')
                wrong_nameL.append(item)
    old_nameD[str(year)+'年财报旧名'] = old_nameL
    wrong_nameD[str(year)+'年财报'] = wrong_nameL
    if year >= 2020:
        break
    
Total_name = [old_nameD, wrong_nameD]

300723：2018年年度报告.pdf已更改
300591：2018年年度报告.pdf已更改
300710：2018年年度报告.pdf已更改
300698：2018年年度报告.pdf已更改
300282：2018年年度报告.pdf已更改
300625：2018年年度报告.pdf已更改
300123：2018年年度报告.pdf已更改
300673：2018年年度报告.pdf已更改
300529：2018年年度报告.pdf已更改
300251：2018年年度报告.pdf已更改
300451：2018年年度报告.pdf已更改
300688：2018年年度报告.pdf已更改
300161：2018年年度报告.pdf已更改
300717：2018年年度报告.pdf已更改
300074：2018年年度报告.pdf已更改
300291：2018年年度报告.pdf已更改
300133：2018年年度报告.pdf已更改
300755：2018年年度报告.pdf已更改
300027：2018年年度报告.pdf已更改
300071：2018年年度报告.pdf已更改
300548：2018年年度报告(更新后).pdf已更改
300622：2018年年度报告.pdf已更改
300363：2018年年度报告.pdf已更改
300321：2018年年度报告.pdf已更改
300538：2018年年度报告.pdf已更改
300426：2018年年度报告(更新后).pdf已更改
300388：2018年年度报告.pdf已更改
300661：2018年年度报告.pdf已更改
300670：2018年年度报告.pdf已更改
300362：2018年年度报告.pdf已更改
300067：2018年年度报告.pdf已更改
300144：2018年年度报告.pdf已更改
300612：2018年年度报告.pdf已更改
300671：2018年年度报告.pdf已更改
300613：2018年年度报告.pdf已更改
300492：2018年年度报告.pdf已更改
300547：2018年年度报告.pdf已更改
300505：2018年年度报告.pdf已更改
300528：2018年年度报告.pdf已更改
300711：2018年年度报告(更新后).pdf已更改
300711：2018年年度报告.pdf已更改
3

## 总结